In [8]:
kerr_dir = '/work/yifan.wang/ringdown/t10-4ogc-run/kerr_220_221.ini'
set_toffset = False
events_dir = './t2_220_221/events.ini'

In [9]:
import numpy as np
import os,sys,glob,h5py

from pycbc.inference.io import loadfile
from pycbc.workflow import WorkflowConfigParser
from configparser import ConfigParser
from pycbc import pnutils
import lal

# Read SNR file

In [10]:
import json
f = open('/work/yifan.wang/ringdown/snrs.json')
snrs = json.load(f)

In [11]:
events = []
for key in snrs:
    if snrs[key]>4:
        events.append(key)

In [12]:
len(events)

50

# Read in the maxL parameters

In [13]:
def gwinfo(name):
    # read in the 4-OGC posterior files
    h5file = glob.glob('/work/yifan.wang/4ogc/release_prod/convertsnr/mixed_posterior/'+name+'.hdf')
    # if not found
    #print(h5file)
    if np.size(h5file)!=1:
        print('Error!!!')
        sys.exit(1)
    f = h5py.File(h5file[0],'r')
    # ra, dec, mass
    try:
        maxl_i = np.argmax(f['samples']['maxl_loglr'][:])
    except KeyError:
        print('KeyError')
        sys.exit(1)
    ra = f['samples']['ra'][maxl_i]
    dec = f['samples']['dec'][maxl_i]
    tref = f['samples']['delta_tc'][maxl_i] + f.attrs['trigger_time']
    m1 = f['samples']['srcmass1'][maxl_i]
    m2 = f['samples']['srcmass2'][maxl_i]
    redshift = f['samples']['redshift'][maxl_i]
    mtotal = (m1+m2)*(1+redshift)
    # starting time = merger time + 10 M_f 
    # toffset = 10* final_mass * lal.MTSUN_SI
    #final_freq = pnutils.get_final_freq('SEOBNRv4',m1,m2,spin1z,spin2z)
    f.close()
    return ra,dec,tref,mtotal

# Write the events.ini

In [14]:
# a new file
try:
    os.remove(events_dir)
except FileNotFoundError:
    pass

with open(events_dir, 'w') as t:
    for gwname in events:
        print(gwname)
        ra,dec,tref,mtotal = gwinfo(gwname)
        
        #1. read in data.ini
        if float(gwname[2:8])<180000:#O1/2 events
            #the o1/2 events' data-GWXXYYZZ.ini files' nameing are kind of complicated.
            #For GWTC-1 events, the name only contains GWYYMMDD, but for o1/2 events detected by 4ogc
            #the naming is GWYYMMDD-HHMMSS, therefore I use "*.ini" trick here
            datadir = glob.glob('data_config/data-'+str(gwname[:8])+'*.ini')
        else:
            datadir = glob.glob('data_config/data-'+str(gwname)+'.ini')
            
        if np.size(datadir)==0:
            print('Data config file not found!!!')
            sys.exit(1)
        
        #2. start to write the events.ini
        t.write('[event-'+str(gwname)+']\n')
        t.write('label='+str(gwname)+'\n')
        t.write('config-files=/work/yifan.wang/ringdown/t10-4ogc-run/'+str(datadir[0])+'\n')
        t.write('\t\t\t'+str(kerr_dir)+'\n')
        t.write('config-overrides =data:trigger-time:'+str(tref)+'\n')
        t.write('\t\t\tstatic_params:ra:'+str(ra)+'\n')
        t.write('\t\t\tstatic_params:dec:'+str(dec)+'\n')
        if mtotal < 150:
            t.write('\t\t\tprior-final_mass:min-final_mass:10\n')
            t.write('\t\t\tprior-final_mass:max-final_mass:300\n')
        else:
            t.write('\t\t\tprior-final_mass:min-final_mass:30\n')
            t.write('\t\t\tprior-final_mass:max-final_mass:500\n')
            
        #3. add the PSD

        config_dir = glob.glob('/work/yifan.wang/4ogc/release_prod/allconfig/*/*'+gwname[2:]+'*.ini')
        print(config_dir)
        cp = WorkflowConfigParser(config_dir)
        t.write('\t\t\t data:psd-start-time:"'+cp.get('data','psd-start-time')+'" \n')
        t.write('\t\t\t data:psd-end-time:"'+cp.get('data','psd-end-time')+'"\n')
        t.write('\n')
t.close()

GW150914_095045
['/work/yifan.wang/4ogc/release_prod/allconfig/shilpa_config/inference-gw150914_095045_XPHM.ini', '/work/yifan.wang/4ogc/release_prod/allconfig/localcopy/inference-gw150914_095045_XPHM.ini']
GW170104_101158
['/work/yifan.wang/4ogc/release_prod/allconfig/sumit_config/inference-gw170104_101158.ini', '/work/yifan.wang/4ogc/release_prod/allconfig/localcopy/inference-gw170104_101158.ini']
GW170121_212536
['/work/yifan.wang/4ogc/release_prod/allconfig/localcopy/inference-GW170121_212536.ini', '/work/yifan.wang/4ogc/release_prod/allconfig/yifan_config/inference-GW170121_212536.ini']
GW170403_230611
['/work/yifan.wang/4ogc/release_prod/allconfig/shichao_config/inference-GW170403_230611.ini', '/work/yifan.wang/4ogc/release_prod/allconfig/localcopy/inference-GW170403_230611.ini']
GW170727_010430
['/work/yifan.wang/4ogc/release_prod/allconfig/shichao_config/inference-GW170727_010430.ini', '/work/yifan.wang/4ogc/release_prod/allconfig/localcopy/inference-GW170727_010430.ini']
GW170

['/work/yifan.wang/4ogc/release_prod/allconfig/sumit_config/inference-gw200129_065458.ini', '/work/yifan.wang/4ogc/release_prod/allconfig/localcopy/inference-gw200129_065458.ini']
GW200208_130117
['/work/yifan.wang/4ogc/release_prod/allconfig/sumit_config/inference-gw200208_130117.ini', '/work/yifan.wang/4ogc/release_prod/allconfig/localcopy/inference-gw200208_130117.ini']
GW200209_085452
['/work/yifan.wang/4ogc/release_prod/allconfig/sumit_config/inference-gw200209_085452.ini', '/work/yifan.wang/4ogc/release_prod/allconfig/localcopy/inference-gw200209_085452.ini']
GW200216_220804
['/work/yifan.wang/4ogc/release_prod/allconfig/sumit_config/inference-gw200216_220804.ini', '/work/yifan.wang/4ogc/release_prod/allconfig/localcopy/inference-gw200216_220804.ini']
GW200224_222234
['/work/yifan.wang/4ogc/release_prod/allconfig/shilpa_config/inference-gw200224_222234_XPHM.ini', '/work/yifan.wang/4ogc/release_prod/allconfig/localcopy/inference-gw200224_222234_XPHM.ini']
GW200302_015811
['/work/y

# Create data file for 4-OGC only events

In [66]:
for gwname in events:
    #print(gwname)
       
    #1. read in data.ini
    if float(gwname[2:8])<180000:#O1/2 events
        datadir = glob.glob('./data_config/data-'+str(gwname[:8])+'*.ini')
    else:
        datadir = glob.glob('./data_config/data-'+str(gwname)+'.ini')
    #print(datadir)
        
    if np.size(datadir)==0:
        print(gwname)
        print('Data config file not found in LVK events, use my own data file')
        datadir = glob.glob('/work/yifan.wang/4ogc/release_prod/allconfig/*/*'+gwname[2:]+'*.ini')
        cp = WorkflowConfigParser(datadir)
        output_dir = 'data_config/4ogc_only_events/data-'+str(gwname)+'.ini'
        try:
            os.remove(output_dir)
        except FileNotFoundError:
            pass
        with open(output_dir, 'w') as t:
            t.write('[data]\n')
            t.write('instruments = '+cp.get('data','instruments')+'\n')
            t.write('trigger-time = '+cp.get('data','trigger-time')+'\n')
            try:
                t.write('frame-type = '+cp.get('data','frame-type')+'\n')
            except:
                t.write('frame-files = '+cp.get('data','frame-files')+'\n')
            t.write('channel-name = '+cp.get('data','channel-name')+'\n')
            t.close()